In [217]:
import numpy as np
import pandas as pd 
import plotly.express as px

In [ ]:
def smooth(arr, k):
    for i in range(0,len(arr)-k):
        for j in range(0,k):
            arr[i] = 

In [399]:
def running_mean(x, N):
    cumsum = np.cumsum(np.insert(x, 0, 0))
    return (cumsum[N:] - cumsum[:-N]) / float(N)

In [218]:
def line_gen(t, length, xyz, rp, N, noise_level):

    t = np.linspace(0,t,N)
    z = np.linspace(0, length, N) + (2*np.random.rand(N)-1)*noise_level
    x = np.zeros(N) + (2*np.random.rand(N)-1)*noise_level
    y = np.zeros(N) + (2*np.random.rand(N)-1)*noise_level
    vector = np.vstack([x,y,z])

    rp = np.array(rp)/180*np.pi

    roll = np.array([[1, 0, 0],
                     [0, np.cos(rp[0]), -np.sin(rp[0])],
                     [0, np.sin(rp[0]), np.cos(rp[0])]], dtype=float)

    pitch = np.array([[np.cos(rp[1]), 0, np.sin(rp[1])],
                      [0, 1, 0],
                      [-np.sin(rp[1]), 0, np.cos(rp[1])]], dtype=float)
    
    vector = roll @ pitch @ vector

    vector[0] = vector[0] + xyz[0]
    vector[1] = vector[1] + xyz[1]
    vector[2] = vector[2] + xyz[2]

    vector = np.vstack([t, vector])

    return vector.T

In [428]:
def angle_gen(t, length_1, length_2, angle, xyz, rpy, N, noise_level):

    v1 = line_gen(t/2, length_1, [0,0,0], [0,0], round(N/2), noise_level)[:,1:]
    v2 = line_gen(t/2, length_2, [v1.T[0][-1],v1.T[1][-1],v1.T[2][-1]], [angle,0], N-round(N/2), noise_level)[:,1:]

    vector = np.vstack([v1,v2])

    rpy = np.array(rpy)/180*np.pi

    roll = np.array([[1, 0, 0],
                     [0, np.cos(rpy[0]), -np.sin(rpy[0])],
                     [0, np.sin(rpy[0]), np.cos(rpy[0])]], dtype=float)
    
    pitch = np.array([[np.cos(rpy[1]), 0, np.sin(rpy[1])],
                      [0, 1, 0],
                      [-np.sin(rpy[1]), 0, np.cos(rpy[1])]], dtype=float)

    yaw = np.array([[np.cos(rpy[2]), -np.sin(rpy[2]), 0],
                    [np.sin(rpy[2]), np.cos(rpy[2]), 0],
                    [0, 0, 1]], dtype=float)
    
    vector = roll @ pitch @ yaw @ vector.T 
    vector = vector.T

    vector.T[0] = vector.T[0] + xyz[0]
    vector.T[1] = vector.T[1] + xyz[1]
    vector.T[2] = vector.T[2] + xyz[2]

    a = running_mean(vector.T[0], 30)
    b = running_mean(vector.T[1], 30)
    c = running_mean(vector.T[2], 30)

    time = np.linspace(0,t,len(a.T))

    vector = np.hstack([time.reshape(-1,1),a.reshape(-1,1),b.reshape(-1,1),c.reshape(-1,1)])
    # vector = np.hstack([time.reshape(-1,1), vector])
    
    return vector

In [221]:
def parab_gen(t, width, height, r, xyz, rpy, N, noise_level):
    
    y0 = -width*r
    a = -height/(y0**2)
    z0 = height

    t = np.linspace(0,t,N)
    x = np.zeros(N) + (2*np.random.rand(N)-1)*noise_level
    y = np.linspace(0, width, N) + (2*np.random.rand(N)-1)*noise_level
    z = a*(y+y0)**2 + z0

    vector = np.vstack([x,y,z])

    rpy = np.array(rpy)/180*np.pi

    roll = np.array([[1, 0, 0],
                     [0, np.cos(rpy[0]), -np.sin(rpy[0])],
                     [0, np.sin(rpy[0]), np.cos(rpy[0])]], dtype=float)
    
    pitch = np.array([[np.cos(rpy[1]), 0, np.sin(rpy[1])],
                      [0, 1, 0],
                      [-np.sin(rpy[1]), 0, np.cos(rpy[1])]], dtype=float)

    yaw = np.array([[np.cos(rpy[2]), -np.sin(rpy[2]), 0],
                    [np.sin(rpy[2]), np.cos(rpy[2]), 0],
                    [0, 0, 1]], dtype=float)
    
    vector = roll @ pitch @ yaw @ vector 

    vector[0] = vector[0] + xyz[0]
    vector[1] = vector[1] + xyz[1]
    vector[2] = vector[2] + xyz[2]
 
    vector = np.vstack([t,vector])

    return vector.T

In [222]:
def giper_gen(t, width, height, r, xyz, rpy, N, noise_level):
    
    y0 = -width*r
    a = height/((width+y0)**3 - y0**3)
    z0 = -a*y0**3

    t = np.linspace(0,t,N)
    x = np.zeros(N) + (2*np.random.rand(N)-1)*noise_level
    y = np.linspace(0, width, N) + (2*np.random.rand(N)-1)*noise_level
    z = a*(y+y0)**3 + z0

    vector = np.vstack([x,y,z])

    rpy = np.array(rpy)/180*np.pi

    roll = np.array([[1, 0, 0],
                     [0, np.cos(rpy[0]), -np.sin(rpy[0])],
                     [0, np.sin(rpy[0]), np.cos(rpy[0])]], dtype=float)
    
    pitch = np.array([[np.cos(rpy[1]), 0, np.sin(rpy[1])],
                      [0, 1, 0],
                      [-np.sin(rpy[1]), 0, np.cos(rpy[1])]], dtype=float)

    yaw = np.array([[np.cos(rpy[2]), -np.sin(rpy[2]), 0],
                    [np.sin(rpy[2]), np.cos(rpy[2]), 0],
                    [0, 0, 1]], dtype=float)
    
    vector = roll @ pitch @ yaw @ vector 

    vector[0] = vector[0] + xyz[0]
    vector[1] = vector[1] + xyz[1]
    vector[2] = vector[2] + xyz[2]

    vector = np.vstack([t,vector])

    return vector.T

In [223]:
def circle_gen(t, R, width, height, rotation, xyz, rpy, N, noise_level):

    p = np.linspace(0, 2*np.pi+np.pi/12, N)
    t = np.linspace(0,t,N)
    x = np.zeros(N) + (2*np.random.rand(N)-1)*noise_level
    y = R*np.cos(p) + (2*np.random.rand(N)-1)*noise_level
    z = R*np.sin(p) + (2*np.random.rand(N)-1)*noise_level

    rotation /= 180/np.pi

    rotation = np.array([[1, 0, 0],
                         [0, np.cos(rotation), -np.sin(rotation)],
                         [0, np.sin(rotation),  np.cos(rotation)]], dtype=float)

    vector = np.vstack([x,y,z])

    vector = rotation @ vector

    vector[1] *= width
    vector[2] *= height

    rpy = np.array(rpy)/180*np.pi

    roll = np.array([[1, 0, 0],
                     [0, np.cos(rpy[0]), -np.sin(rpy[0])],
                     [0, np.sin(rpy[0]), np.cos(rpy[0])]], dtype=float)
    
    pitch = np.array([[np.cos(rpy[1]), 0, np.sin(rpy[1])],
                      [0, 1, 0],
                      [-np.sin(rpy[1]), 0, np.cos(rpy[1])]], dtype=float)

    yaw = np.array([[np.cos(rpy[2]), -np.sin(rpy[2]), 0],
                    [np.sin(rpy[2]), np.cos(rpy[2]), 0],
                    [0, 0, 1]], dtype=float)
    
    vector = roll @ pitch @ yaw @ vector
    vector[0] = vector[0] + xyz[0]
    vector[1] = vector[1] + xyz[1]
    vector[2] = vector[2] + xyz[2]

    vector = np.vstack([t,vector])

    return vector.T

In [224]:
def spiral_gen(t, R, turn, width, height, rotation, xyz, rpy, N, noise_level):

    t = np.linspace(0,t,N)
    p = np.linspace(0, 2*np.pi*turn+np.pi/12, N)
    r = np.linspace(R[0], R[1], N)
    x = np.zeros(N) + (2*np.random.rand(N)-1)*noise_level
    y = r*np.cos(p) + (2*np.random.rand(N)-1)*noise_level
    z = r*np.sin(p) + (2*np.random.rand(N)-1)*noise_level

    rotation /= 180/np.pi

    rotation = np.array([[1, 0, 0],
                         [0, np.cos(rotation), -np.sin(rotation)],
                         [0, np.sin(rotation),  np.cos(rotation)]], dtype=float)

    vector = np.vstack([x,y,z])

    vector = rotation @ vector

    vector[1] *= width
    vector[2] *= height

    rpy = np.array(rpy)/180*np.pi

    roll = np.array([[1, 0, 0],
                     [0, np.cos(rpy[0]), -np.sin(rpy[0])],
                     [0, np.sin(rpy[0]), np.cos(rpy[0])]], dtype=float)
    
    pitch = np.array([[np.cos(rpy[1]), 0, np.sin(rpy[1])],
                      [0, 1, 0],
                      [-np.sin(rpy[1]), 0, np.cos(rpy[1])]], dtype=float)

    yaw = np.array([[np.cos(rpy[2]), -np.sin(rpy[2]), 0],
                    [np.sin(rpy[2]), np.cos(rpy[2]), 0],
                    [0, 0, 1]], dtype=float)
    
    vector = roll @ pitch @ yaw @ vector 

    vector[0] = vector[0] + xyz[0]
    vector[1] = vector[1] + xyz[1]
    vector[2] = vector[2] + xyz[2]

    vector = np.vstack([t,vector])

    return vector.T

In [225]:
line = line_gen(10,1,[1,1,1], [45,45],100,0.0)
data = pd.DataFrame(data=line,columns=['t', 'X', 'Y', 'Z'])

In [434]:
line1 = angle_gen(10, 2, 1, 90, [1,1,1], [0,0,0], 200, 0.0)
data = pd.DataFrame(data=line1,columns=['t', 'X', 'Y', 'Z'])

In [227]:
line2 = parab_gen(15, 1, -2, 0.5, [1,1,1], [90,45,45], 200, 0.0)
data = pd.DataFrame(data=line2,columns=['t', 'X', 'Y', 'Z'])
# line2

In [228]:
line3 = giper_gen(20, 1, 2, 0.0, [0,0,0], [0,0,0], 200, 0.0)
data = pd.DataFrame(data=line3,columns=['t', 'X', 'Y', 'Z'])
# line3

In [229]:
line4 = circle_gen(30, 1, 2, 1, 0, [0,0,1], [90,45,45], 500, 0.01)
data = pd.DataFrame(data=line4,columns=['t', 'X', 'Y', 'Z'])
# line4

In [230]:
line5 = spiral_gen(30, [1,2], 10, 1, 1, 45, [0,0,1], [90,45,45], 500, 0.01)
data = pd.DataFrame(data=line5,columns=['t', 'X', 'Y', 'Z'])
# line5

In [433]:
fig = px.line_3d(data, x="X", y="Y", z="Z", markers=False)
fig.show()

## Палочки

### Трейн

In [357]:
NUM_DASH = 20

INTERVAL_L = [3000,10000,1] # мм
INTERVAL_X = [-10000,10000,1] 
INTERVAL_Y = [-10000,10000,1] 
INTERVAL_Z = [-5000,5000,1] 

INTERVAL_N = [500,600,1]


In [358]:
dash = line_gen(12500,5,[0,0,0],[0,0],500,0.02)

dash = pd.DataFrame(data=dash,columns=['t', 'X', 'Y', 'Z'])
dash['I'] = 0
 
for i in range(1,NUM_DASH):
    temp_line = line_gen(12500,
                         np.random.randint(*INTERVAL_L)[0]/1000,
                         [np.random.randint(*INTERVAL_X)[0]/1000, np.random.randint(*INTERVAL_Y)[0]/1000, np.random.randint(*INTERVAL_Z)[0]/1000],
                         [0,0],
                         np.random.randint(*INTERVAL_N)[0],
                         0.02
                         )
    temp = pd.DataFrame(data=temp_line,columns=['t', 'X', 'Y', 'Z'])
    temp["I"] = i
    dash = pd.concat([dash, temp])


In [359]:
fig = px.line_3d(dash, x="X", y="Y", z="Z", color="I", markers=False)
fig.show()

In [360]:
dash.to_csv("dash_lines/dash_par_train.csv", index=False)

### Тест

In [361]:
NUM_DASH_TEST = 20

INTERVAL_L_TEST = [3000,10000,1] # мм
INTERVAL_X_TEST = [-3000,17000,1] 
INTERVAL_Y_TEST = [-16000,4000,1] 
INTERVAL_Z_TEST = [-5000,5000,1] 

INTERVAL_N_TEST = [500,600,1]

In [362]:
dash_test = line_gen(12500,5,[0,0,0],[0,0],500,0.02)

dash_test = pd.DataFrame(data=dash_test,columns=['t', 'X', 'Y', 'Z'])
dash_test['I'] = 0
 
for i in range(1,NUM_DASH_TEST):
    temp_line = line_gen(12500,
                         np.random.randint(*INTERVAL_L_TEST)[0]/1000,
                         [np.random.randint(*INTERVAL_X_TEST)[0]/1000, np.random.randint(*INTERVAL_Y_TEST)[0]/1000, np.random.randint(*INTERVAL_Z_TEST)[0]/1000],
                         [0,0],
                         np.random.randint(*INTERVAL_N_TEST)[0],
                         0.02
                         )
    temp = pd.DataFrame(data=temp_line,columns=['t', 'X', 'Y', 'Z'])
    temp["I"] = i
    dash_test = pd.concat([dash_test, temp])

In [363]:
fig = px.line_3d(dash_test, x="X", y="Y", z="Z", color="I", markers=False)
fig.show()

In [364]:
dash_test.to_csv("dash_lines/dash_par_test.csv", index=False)

## Наклонные палочки

### Трейн

In [365]:
NUM_DASH = 20

INTERVAL_L = [3000,10000,1] # мм
INTERVAL_X = [-10000,10000,1] 
INTERVAL_Y = [-10000,10000,1] 
INTERVAL_Z = [-5000,5000,1] 

INTERVAL_R = [0,180000,1]
INTERVAL_P = [0,180000,1]
INTERVAL_YW = [0,90000,1]

INTERVAL_N = [500,600,1]

In [366]:
dash_slope = line_gen(12500,5,[0,0,0],[0,0],500,0.02)

dash_slope = pd.DataFrame(data=dash_slope,columns=['t', 'X', 'Y', 'Z'])
dash_slope['I'] = 0
 
for i in range(1,NUM_DASH):
    temp_line = line_gen(12500,
                         np.random.randint(*INTERVAL_L)[0]/1000,
                         [np.random.randint(*INTERVAL_X)[0]/1000, np.random.randint(*INTERVAL_Y)[0]/1000, np.random.randint(*INTERVAL_Z)[0]/1000],
                         [np.random.randint(*INTERVAL_R)[0]/1000,np.random.randint(*INTERVAL_P)[0]/1000],
                         np.random.randint(*INTERVAL_N)[0],
                         0.02
                         )
    temp = pd.DataFrame(data=temp_line,columns=['t', 'X', 'Y', 'Z'])
    temp["I"] = i
    dash_slope = pd.concat([dash_slope, temp])

In [367]:
fig = px.line_3d(dash_slope, x="X", y="Y", z="Z", color="I", markers=False)
fig.show()

In [368]:
dash_slope.to_csv("dash_lines/dash_slope_train.csv", index=False)

### Тест

In [369]:
NUM_DASH_TEST = 20

INTERVAL_L_TEST = [3000,10000,1] # мм
INTERVAL_X_TEST = [-3000,17000,1] 
INTERVAL_Y_TEST = [-16000,4000,1] 
INTERVAL_Z_TEST = [-5000,5000,1] 

INTERVAL_R_TEST = [0,180000,1]
INTERVAL_P_TEST = [0,180000,1]
INTERVAL_YW_TEST = [0,90000,1]

INTERVAL_N_TEST = [500,600,1]

In [370]:
dash_slope_test = line_gen(12500,5,[0,0,0],[0,0],500,0.02)

dash_slope_test = pd.DataFrame(data=dash_slope_test,columns=['t', 'X', 'Y', 'Z'])
dash_slope_test['I'] = 0
 
for i in range(1,NUM_DASH_TEST):
    temp_line = line_gen(12500,
                         np.random.randint(*INTERVAL_L_TEST)[0]/1000,
                         [np.random.randint(*INTERVAL_X_TEST)[0]/1000, np.random.randint(*INTERVAL_Y_TEST)[0]/1000, np.random.randint(*INTERVAL_Z_TEST)[0]/1000],
                         [np.random.randint(*INTERVAL_R_TEST)[0]/1000,np.random.randint(*INTERVAL_P_TEST)[0]/1000],
                         np.random.randint(*INTERVAL_N_TEST)[0],
                         0.02
                         )
    temp = pd.DataFrame(data=temp_line,columns=['t', 'X', 'Y', 'Z'])
    temp["I"] = i
    dash_slope_test = pd.concat([dash_slope_test, temp])

In [371]:
fig = px.line_3d(dash_slope_test, x="X", y="Y", z="Z", color="I", markers=False)
fig.show()

In [382]:
dash_slope_test.to_csv("dash_lines/dash_slope_test.csv", index=False)

## Углы

### Трейн

In [444]:
NUM = 20

INTERVAL_L = [3000,10000,1] # мм
INTERVAL_X = [-10000,10000,1] 
INTERVAL_Y = [-10000,10000,1] 
INTERVAL_Z = [-5000,5000,1] 

INTERVAL_A = [70000,135000,1]

INTERVAL_R = [0,180000,1]
INTERVAL_P = [0,180000,1]
INTERVAL_YW = [0,90000,1]

INTERVAL_N = [500,600,1]

In [445]:
angle = angle_gen(12500,2,1,90,[0,0,0],[0,0,0],500,0.02)

angle = pd.DataFrame(data=angle,columns=['t', 'X', 'Y', 'Z'])
angle['I'] = 0
 
for i in range(1,NUM):
    temp_line = angle_gen(12500,
                         np.random.randint(*INTERVAL_L)[0]/1000,
                         np.random.randint(*INTERVAL_L)[0]/1000,
                         np.random.randint(*INTERVAL_A)[0]/1000,
                         [np.random.randint(*INTERVAL_X)[0]/1000, np.random.randint(*INTERVAL_Y)[0]/1000, np.random.randint(*INTERVAL_Z)[0]/1000],
                         [np.random.randint(*INTERVAL_R)[0]/1000,np.random.randint(*INTERVAL_P)[0]/1000,np.random.randint(*INTERVAL_YW)[0]/1000],
                         np.random.randint(*INTERVAL_N)[0],
                         0.02
                         )
    temp = pd.DataFrame(data=temp_line,columns=['t', 'X', 'Y', 'Z'])
    temp["I"] = i
    angle = pd.concat([angle, temp])

In [437]:
fig = px.line_3d(angle, x="X", y="Y", z="Z", color="I", markers=False)
fig.show()

In [438]:
angle.to_csv("dash_lines/angle_train.csv", index=False)

### Тест

In [439]:
NUM_TEST = 20

INTERVAL_L_TEST = [3000,10000,1] # мм
INTERVAL_X_TEST = [-3,17000,1] 
INTERVAL_Y_TEST = [-15000,5000,1] 
INTERVAL_Z_TEST = [-5000,5000,1] 

INTERVAL_A_TEST = [70000,135000,1]

INTERVAL_R_TEST = [0,180000,1]
INTERVAL_P_TEST = [0,180000,1]
INTERVAL_YW_TEST = [0,180000,1]

INTERVAL_N_TEST = [500,600,1]

In [440]:
angle_test = angle_gen(12500,2,1,90,[0,0,0],[0,0,0],500,0.02)

angle_test = pd.DataFrame(data=angle_test,columns=['t', 'X', 'Y', 'Z'])
angle_test['I'] = 0
 
for i in range(1,NUM_TEST):
    temp_line = angle_gen(12500,
                         np.random.randint(*INTERVAL_L_TEST)[0]/1000,
                         np.random.randint(*INTERVAL_L_TEST)[0]/1000,
                         np.random.randint(*INTERVAL_A_TEST)[0]/1000,
                         [np.random.randint(*INTERVAL_X_TEST)[0]/1000, np.random.randint(*INTERVAL_Y_TEST)[0]/1000, np.random.randint(*INTERVAL_Z_TEST)[0]/1000],
                         [np.random.randint(*INTERVAL_R_TEST)[0]/1000,np.random.randint(*INTERVAL_P_TEST)[0]/1000,np.random.randint(*INTERVAL_YW_TEST)[0]/1000],
                         np.random.randint(*INTERVAL_N_TEST)[0],
                         0.02
                         )
    temp = pd.DataFrame(data=temp_line,columns=['t', 'X', 'Y', 'Z'])
    temp["I"] = i
    angle_test = pd.concat([angle_test, temp])

In [441]:
fig = px.line_3d(angle_test, x="X", y="Y", z="Z", color="I", markers=False)
fig.show()

In [442]:
angle_test.to_csv("dash_lines/angle_test.csv", index=False)

## Углы 90

### Трейн

In [443]:
NUM = 20

INTERVAL_L = [3000,10000,1] # мм
INTERVAL_X = [-10000,10000,1] 
INTERVAL_Y = [-10000,10000,1] 
INTERVAL_Z = [-5000,5000,1] 

INTERVAL_R = [0,180000,1]
INTERVAL_P = [0,180000,1]
INTERVAL_YW = [0,90000,1]

INTERVAL_N = [500,600,1]

In [447]:
angle_90 = angle_gen(12500,2,1,90,[0,0,0],[0,0,0],500,0.02)

angle_90 = pd.DataFrame(data=angle_90,columns=['t', 'X', 'Y', 'Z'])
angle_90['I'] = 0
 
for i in range(1,NUM):
    temp_line = angle_gen(12500,
                         np.random.randint(*INTERVAL_L)[0]/1000,
                         np.random.randint(*INTERVAL_L)[0]/1000,
                         90,
                         [np.random.randint(*INTERVAL_X)[0]/1000, np.random.randint(*INTERVAL_Y)[0]/1000, np.random.randint(*INTERVAL_Z)[0]/1000],
                         [np.random.randint(*INTERVAL_R)[0]/1000,np.random.randint(*INTERVAL_P)[0]/1000,np.random.randint(*INTERVAL_YW)[0]/1000],
                         np.random.randint(*INTERVAL_N)[0],
                         0.02
                         )
    temp = pd.DataFrame(data=temp_line,columns=['t', 'X', 'Y', 'Z'])
    temp["I"] = i
    angle_90 = pd.concat([angle_90, temp])

In [448]:
fig = px.line_3d(angle_90, x="X", y="Y", z="Z", color="I", markers=False)
fig.show()

In [449]:
angle_90.to_csv("dash_lines/angle_90_train.csv", index=False)

### Тест

In [450]:
NUM_TEST = 20

INTERVAL_L_TEST = [3000,10000,1] # мм
INTERVAL_X_TEST = [-3,17000,1] 
INTERVAL_Y_TEST = [-15000,5000,1] 
INTERVAL_Z_TEST = [-5000,5000,1] 

INTERVAL_A_TEST = [70000,135000,1]

INTERVAL_R_TEST = [0,180000,1]
INTERVAL_P_TEST = [0,180000,1]
INTERVAL_YW_TEST = [0,180000,1]

INTERVAL_N_TEST = [500,600,1]

In [451]:
angle_90_test = angle_gen(12500,2,1,90,[0,0,0],[0,0,0],500,0.02)

angle_90_test = pd.DataFrame(data=angle_90_test,columns=['t', 'X', 'Y', 'Z'])
angle_90_test['I'] = 0
 
for i in range(1,NUM_TEST):
    temp_line = angle_gen(12500,
                         np.random.randint(*INTERVAL_L_TEST)[0]/1000,
                         np.random.randint(*INTERVAL_L_TEST)[0]/1000,
                         90,
                         [np.random.randint(*INTERVAL_X_TEST)[0]/1000, np.random.randint(*INTERVAL_Y_TEST)[0]/1000, np.random.randint(*INTERVAL_Z_TEST)[0]/1000],
                         [np.random.randint(*INTERVAL_R_TEST)[0]/1000,np.random.randint(*INTERVAL_P_TEST)[0]/1000,np.random.randint(*INTERVAL_YW_TEST)[0]/1000],
                         np.random.randint(*INTERVAL_N_TEST)[0],
                         0.02
                         )
    temp = pd.DataFrame(data=temp_line,columns=['t', 'X', 'Y', 'Z'])
    temp["I"] = i
    angle_90_test = pd.concat([angle_90_test, temp])

In [452]:
fig = px.line_3d(angle_90_test, x="X", y="Y", z="Z", color="I", markers=False)
fig.show()

In [453]:
angle_90_test.to_csv("dash_lines/angle_90_test.csv", index=False)